In [2]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sqlalchemy import create_engine
from sklearn import preprocessing
import mysql.connector
from pandas import DataFrame

### 1. Data

In [3]:
duples_repodb = pd.read_csv("./Data/Input/Drug Repurposing/repoDB_all_disdru.tsv", sep='\t')

In [4]:
duples_csbj = pd.read_csv("./Data/Input/Drug Repurposing/duplas_CSBJ.tsv")

In [5]:
duples_csbj = duples_csbj.drop(["Unnamed: 0"],axis=1)

In [7]:
duples_csbj = duples_csbj.rename(columns={"Disease CUI": "disease_id"})

In [ ]:
dis_path_direct = pd.read_csv('./Data/Input/DISNET/disease_pathway.tsv', sep='\t')

In [9]:
drug_gen = pd.read_csv('./Data/Input/DISNET/drug_gen.tsv', sep='\t')

In [10]:
drug_gen = drug_gen.drop(["Unnamed: 0"],axis=1)

In [25]:
dis_gen = pd.read_csv('./Data/Input/DISNET/dis_genes_gda.tsv', sep='\t')

In [26]:
dis_gen = dis_gen.drop(["Unnamed: 0"],axis=1)

In [46]:
dis_gen_sinfil = pd.read_csv('./Data/Input/DISNET/dis_genes.tsv', sep='\t')

In [47]:
dis_gen_sinfil = dis_gen_sinfil.drop(["Unnamed: 0"],axis=1)

#### JOIN REPODB

In [28]:
dis_drug_path = duples_repodb.merge(dis_path_direct, how='inner', on='disease_id')

In [30]:
dis_drug_path_fil = dis_drug_path.drop(["pathway_id"],axis=1)

In [31]:
dis_drug_path_fil = dis_drug_path_fil.drop_duplicates()

In [33]:
dis_drug_gen = dis_gen.merge(drug_gen, how ="inner", on = "gene_id")

In [34]:
dis_drug_gen = dis_drug_gen.drop_duplicates()

In [36]:
dis_drug_original = dis_drug_path_fil.merge(dis_drug_gen, how = "outer", on =["disease_id","drug_id"])

In [38]:
dis_drug =dis_drug_original.drop_duplicates()[['disease_id','drug_id']].drop_duplicates()

In [100]:
cases_repodb_gda = duples_repodb.merge(dis_drug,how = "inner",on = ["disease_id","drug_id"])

In [102]:
cases_repodb_gda.to_csv("cases_repodb_gda.tsv", sep ="\t")

#### JOIN CSBJ

In [56]:
dis_drug_path_csbj = duples_csbj.merge(dis_path_direct , how = "inner", on = "disease_id")

In [58]:
dis_drug_path_csbj_fil = dis_drug_path_csbj.drop(["pathway_id"],axis=1)

In [59]:
dis_drug_original_csbj = dis_drug_path_csbj_fil.merge(dis_drug_gen, how = "outer", on =["disease_id","drug_id"])

In [61]:
dis_drug_csbj =dis_drug_original_csbj.drop_duplicates()[['disease_id','drug_id']].drop_duplicates()

In [63]:
cases_csbj = duples_csbj.merge(dis_drug_csbj,how = "inner",on = ["disease_id","drug_id"])

In [115]:
cases_csbj.to_csv("cases_csbj.tsv", sep="\t")

### 2. Join pathway-disease with pathway-drug

In [60]:
cases_repodb = pd.read_csv("./Data/Input/DISNET/cases_repodb_gda.tsv", sep='\t')

In [49]:
len(cases_repodb["disease_id"].unique())

55

In [ ]:
len(cases_repodb["disease_id"].unique())

In [40]:
dis_drug_path_num = dis_drug_path

In [50]:
len(dis_drug_path_num["disease_id"].unique())

51

In [42]:
drug_gen_pw = pd.read_csv("./Data/Input/DISNET/drug_gen_pw.tsv", sep='\t')

In [44]:
drug_gen_pw = drug_gen_pw.drop(["Unnamed: 0"],axis=1)

In [ ]:
## 1º Join pws-based DR cases with their pathways

In [46]:
pw_based_DR_pw = cases_repodb.merge(dis_drug_path_num,how = "inner",on = ["disease_id","drug_id"])

In [51]:
len(pw_based_DR_pw["disease_id"].unique())

51

In [ ]:
## 2º Join with drug and pathway-target

In [52]:
final = pw_based_DR_pw.merge(drug_gen_pw,how = "inner",on = ["pathway_id","drug_id"])

In [55]:
final_cases_repodb =final.drop_duplicates()

In [ ]:
dis_drug_path_num = dis_drug_path_num.groupby(['disease_id', 'drug_id']).count()

In [59]:
final_cases_repodb.to_csv("final_cases_repodb.tsv", sep='\t')

In [7]:
final_cases_repodb = pd.read_csv("./Data/Input/DISNET/final_cases_repodb.tsv", sep='\t')

In [61]:
cases_csbj = pd.read_csv("./Data/Input/DISNET/cases_csbj_gda.tsv", sep='\t')

In [63]:
cases_csbj = cases_csbj.drop(["Unnamed: 0"],axis=1)

In [65]:
pw_based_DR_pw_csbj = cases_csbj.merge(dis_drug_path_num,how = "inner",on = ["disease_id","drug_id"])

In [67]:
final_csbj = pw_based_DR_pw_csbj.merge(drug_gen_pw,how = "inner",on = ["pathway_id","drug_id"])

In [69]:
final_csbj.to_csv("final_cases_csbj.tsv", sep='\t')

### 3. Number of pathways shared between disease and drug 

In [5]:
cases_csbj = pd.read_csv("./Data/Input/DISNET/final_cases_csbj.tsv", sep='\t')

In [6]:
cases_csbj = cases_csbj.drop(["Unnamed: 0"],axis=1)

In [9]:
cases_csbj_num = cases_csbj.groupby(['disease_id', 'drug_id']).count()

In [11]:
cases_repodb = pd.read_csv("./Data/Input/DISNET/final_cases_repodb.tsv", sep='\t')

In [12]:
cases_repodb = cases_repodb.drop(["Unnamed: 0"],axis=1)

In [15]:
cases_repodb_pw = cases_repodb.drop(["gene_id"],axis=1)

In [38]:
cases_repodb_pw = cases_repodb_pw.drop_duplicates()

In [39]:
cases_repodb_pw_num = cases_repodb_pw.groupby(['disease_id', 'drug_id']).count()

In [40]:
cases_repodb_pw_num.to_csv("cases_repodb_pw_num.tsv", sep='\t')

In [41]:
cases_repodb_pw_num = pd.read_csv("./Data/Input/DISNET/cases_repodb_pw_num.tsv", sep='\t')

In [42]:
cases_repodb_pw_num["pathway_id"].mean()

1.4565217391304348

In [43]:
cases_repodb_pw_num.describe()

pathway_id
count   46.000000
mean     1.456522
std      0.503610
min      1.000000
25%      1.000000
50%      1.000000
75%      2.000000
max      2.000000